In [1]:
### How to make api call
import requests
import json

def make_api_call(latitude,longitude,apikey):
    url = f"https://api.openweathermap.org/data/2.5/weather?lat={latitude}&lon={longitude}&appid={apikey}"
    try:
      response = requests.get(url)
    except requests.exceptions.RequestException as e:
      print(f"Error recibiendo los datos: {e}")
      return None
    weather_data = response.json()
    return weather_data

In [2]:
apikey = '8b47fab30f52065a6468746c614f997f'
lat = 40.781722
lon = -73.973056

wheatherData = make_api_call(lat,lon,apikey)

###Imprimir JSON de informacion
print(wheatherData)

{'coord': {'lon': -73.9713, 'lat': 40.7831}, 'weather': [{'id': 800, 'main': 'Clear', 'description': 'clear sky', 'icon': '01d'}], 'base': 'stations', 'main': {'temp': 282.17, 'feels_like': 280.15, 'temp_min': 279.75, 'temp_max': 284.56, 'pressure': 1024, 'humidity': 52}, 'visibility': 10000, 'wind': {'speed': 3.6, 'deg': 260}, 'clouds': {'all': 0}, 'dt': 1712580488, 'sys': {'type': 1, 'id': 5141, 'country': 'US', 'sunrise': 1712572022, 'sunset': 1712618863}, 'timezone': -14400, 'id': 5125771, 'name': 'Manhattan', 'cod': 200}


In [6]:
import pandas as pd

df = pd.read_csv("C:/Users/jusec/OneDrive/Documentos/GitHub/Proyecto-Procesamiento-de-Datos/NYPD_Arrest_Data__Year_to_Date__20240322.csv")

In [7]:
df.describe()

ARREST_KEY          PD_CD          KY_CD  ARREST_PRECINCT  \
count  2.268720e+05  226870.000000  226855.000000    226872.000000   
mean   2.706479e+08     424.754401     249.345132        63.430529   
std    5.304010e+06     274.475381     147.686733        34.635045   
min    2.611809e+08       1.000000     101.000000         1.000000   
25%    2.661655e+08     114.000000     113.000000        40.000000   
50%    2.707012e+08     397.000000     236.000000        62.000000   
75%    2.752159e+08     705.000000     344.000000       101.000000   
max    2.797797e+08     997.000000     995.000000       123.000000   

       JURISDICTION_CODE    X_COORD_CD     Y_COORD_CD       Latitude  \
count      226872.000000  2.268720e+05  226872.000000  226872.000000   
mean            0.928537  1.005787e+06  208289.084321      40.738154   
std             7.538569  2.150944e+04   29744.718873       0.118237   
min             0.000000  0.000000e+00       0.000000       0.000000   
25%             0.000000  9.913475e+05  186051.250000      40.677251   
50%             0.000000  1.005407e+06  206887.000000      40.734456   
75%             0.000000  1.017925e+06  236149.000000      40.814845   
max            97.000000  1.067220e+06  271819.000000      40.912714   

           Longitude  
count  226872.000000  
mean      -73.921915  
std         0.173338  
min       -74.253256  
25%       -73.974396  
50%       -73.923618  
75%       -73.878486  
max         0.000000

In [8]:
import folium as fl
from folium.plugins import HeatMap

m = fl.Map(location = [40.738154,-73.921915])

haetmap = HeatMap(list((zip(df['Latitude'],df['Longitude']))),
                min_opacity=0.2,
                radius=50, blur=50, 
                max_zoom=1
                )

haetmap.add_to(m)
m

In [9]:
### Crear el mapa
latitude = 40.7382
longitude = -73.9219


m = fl.Map(location=[latitude, longitude], zoom_start=10)

# Datos de ejemplo para un punto en el tiempo
forecast_example = make_api_call(latitude,longitude,apikey)


# Formato del texto del marcador
popup_text = f"""
Fecha y hora: {forecast_example['dt']}<br>
Temperatura: {forecast_example['main']['temp']} K<br>
Presión: {forecast_example['main']['pressure']} hPa<br>
Humedad: {forecast_example['main']['humidity']}%<br>
Clima: {forecast_example['weather'][0]['main']} ({forecast_example['weather'][0]['description']})<br>
Velocidad del viento: {forecast_example['wind']['speed']} m/s<br>
"""

 #Agregar un marcador al mapa
fl.Marker(
    [latitude, longitude],
    popup=fl.Popup(html=popup_text, max_width=250)
).add_to(m)


# Mostrar el mapa
m

In [10]:
###Agrupar por barrios y sacar promedios

latdic = dict(df.groupby(['ARREST_BORO'])['Latitude'].mean())

londic = dict(df.groupby(['ARREST_BORO'])['Longitude'].mean())

print(latdic,londic , sep='\n')


{'B': 40.842336551776924, 'K': 40.65929330809888, 'M': 40.771409056657504, 'Q': 40.71504591174004, 'S': 40.61131624332839}
{'B': -73.8909266020233, 'K': -73.94753174177487, 'M': -73.96970222125222, 'Q': -73.830016519732, 'S': -74.117971159588}


In [11]:
###Crear los marcadores en el mapa
latitude = 40.7382
longitude = -73.9219


boro_dic = {
    'B':'Bronx',
    'S':'Sataten Island',
    'K':'Brooklyn',
    'M':'Manhattan',
    'Q':'Queens'
}

m = fl.Map(location = [latitude, longitude] , zoom_start=10)

for lat,lon in zip(latdic,londic):
    # Datos de ejemplo para un punto en el tiempo
    forecast_example = make_api_call(latdic[lat],londic[lon],apikey)


    # Formato del texto del marcador
    popup_text = f"""
    Fecha y hora: {forecast_example['dt']}<br>
    Temperatura: {forecast_example['main']['temp']} K<br>
    Presión: {forecast_example['main']['pressure']} hPa<br>
    Humedad: {forecast_example['main']['humidity']}%<br>
    Clima: {forecast_example['weather'][0]['main']} ({forecast_example['weather'][0]['description']})<br>
    Velocidad del viento: {forecast_example['wind']['speed']} m/s<br>
    Barrio: {boro_dic[lat]}
    """

    #Agregar un marcador al mapa
    fl.Marker(
        [latdic[lat], londic[lon]],
        popup=fl.Popup(html=popup_text, max_width=250)
    ).add_to(m)


    # Mostrar el mapa
m